In [1]:
%pip install kagglehub
%pip install matplotlib

Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.


In [2]:
import kagglehub
import email

/home/morrissimons/miniconda3/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [3]:


# Download latest version
path = kagglehub.dataset_download("wcukierski/enron-email-dataset")

print("Path to dataset files:", path)

Path to dataset files: /home/morrissimons/.cache/kagglehub/datasets/wcukierski/enron-email-dataset/versions/2


In [ ]:
import pandas as pd

# The Enron dataset typically has a emails.csv file in the dataset
df = pd.read_csv(f"{path}/emails.csv")
df.head()

In [5]:
first_email = df.iloc[1] 
print("File:", first_email['file'])
print("\nMessage:", first_email['message'])


File: allen-p/_sent_mail/10.

Message: Message-ID: <15464986.1075855378456.JavaMail.evans@thyme>
Date: Fri, 4 May 2001 13:51:00 -0700 (PDT)
From: phillip.allen@enron.com
To: john.lavorato@enron.com
Subject: Re:
Mime-Version: 1.0
Content-Type: text/plain; charset=us-ascii
Content-Transfer-Encoding: 7bit
X-From: Phillip K Allen
X-To: John J Lavorato <John J Lavorato/ENRON@enronXgate@ENRON>
X-cc: 
X-bcc: 
X-Folder: \Phillip_Allen_Jan2002_1\Allen, Phillip K.\'Sent Mail
X-Origin: Allen-P
X-FileName: pallen (Non-Privileged).pst

Traveling to have a business meeting takes the fun out of the trip.  Especially if you have to prepare a presentation.  I would suggest holding the business plan meetings here then take a trip without any formal business meetings.  I would even try and get some honest opinions on whether a trip is even desired or necessary.

As far as the business meetings, I think it would be more productive to try and stimulate discussions across the different groups about what is 

In [6]:
print(f"Total number of emails in the dataset: {len(df):,}")

Total number of emails in the dataset: 517,401


In [7]:
# Extract Message-IDs from the message column using string operations
message_ids = df['message'].str.extract(r'Message-ID: <([^>]+)>', expand=False)
print(message_ids.unique()[0])
print(len(message_ids.unique()))

18782981.1075855378110.JavaMail.evans@thyme
517401


In [8]:
print(df['message'][0])

Message-ID: <18782981.1075855378110.JavaMail.evans@thyme>
Date: Mon, 14 May 2001 16:39:00 -0700 (PDT)
From: phillip.allen@enron.com
To: tim.belden@enron.com
Subject: 
Mime-Version: 1.0
Content-Type: text/plain; charset=us-ascii
Content-Transfer-Encoding: 7bit
X-From: Phillip K Allen
X-To: Tim Belden <Tim Belden/Enron@EnronXGate>
X-cc: 
X-bcc: 
X-Folder: \Phillip_Allen_Jan2002_1\Allen, Phillip K.\'Sent Mail
X-Origin: Allen-P
X-FileName: pallen (Non-Privileged).pst

Here is our forecast

 


In [9]:
e = email.message_from_string(df['message'][0])

for items in e.items():
    print(items)


print("="*80)

print("\n" + e.get_payload())

('Message-ID', '<18782981.1075855378110.JavaMail.evans@thyme>')
('Date', 'Mon, 14 May 2001 16:39:00 -0700 (PDT)')
('From', 'phillip.allen@enron.com')
('To', 'tim.belden@enron.com')
('Subject', '')
('Mime-Version', '1.0')
('Content-Type', 'text/plain; charset=us-ascii')
('Content-Transfer-Encoding', '7bit')
('X-From', 'Phillip K Allen')
('X-To', 'Tim Belden <Tim Belden/Enron@EnronXGate>')
('X-cc', '')
('X-bcc', '')
('X-Folder', "\\Phillip_Allen_Jan2002_1\\Allen, Phillip K.\\'Sent Mail")
('X-Origin', 'Allen-P')
('X-FileName', 'pallen (Non-Privileged).pst')

Here is our forecast

 


In [11]:
def check_payload(message_str):
    msg = email.message_from_string(message_str)
    return bool(msg.get_payload())

def check_payload_length(message_str):
    msg = email.message_from_string(message_str)
    return len(msg.get_payload())

# Apply the function to all messages and count those with payloads
has_payload = df['message'].apply(check_payload)
payload_lengths = df['message'].apply(check_payload_length)
print(f"Emails with payload: {sum(has_payload):,} out of {len(df):,}")
print(f"smallest payload: {min(payload_lengths)}")

Emails with payload: 517,401 out of 517,401
smallest payload: 1


In [32]:
import re

def find_ssn(message_str):
    msg = email.message_from_string(message_str)
    payload = msg.get_payload()
    pattern = r"^\d{3}-\d{2}-\d{4}$"
    for line in payload.splitlines():
        if re.search(pattern, line):
            return line
    return None

df['ssn'] = df['message'].apply(find_ssn)


In [16]:
print(df['ssn'].dropna().unique())
print(len(df['ssn'].dropna().unique()))

['522-94-9373' '262-64-0939' '454-69-0782' '465-47-0999' '085-62-2348'
 '458-42-0815' '643-64-9183' '456-92-6014' '464-41-6228' '458-37-4132']
10


In [15]:
# Get the unique indices where SSNs were found
ssn_indices = df['ssn'].dropna().index

# Display full messages for each email containing an SSN
for idx in ssn_indices:
    print(f"\n{'='*80}")
    print(f"Index: {idx}")
    print(f"SSN found: {df['ssn'][idx]}")
    print(f"File: {df['file'][idx]}")
    print(f"\nFull message:")
    print(f"{'='*80}")
    print(df['message'][idx])
    print(f"{'='*80}\n")


Index: 40064
SSN found: 522-94-9373
File: campbell-l/_sent_mail/167.

Full message:
Message-ID: <22495509.1075857891273.JavaMail.evans@thyme>
Date: Tue, 25 Jul 2000 08:11:00 -0700 (PDT)
From: larry.campbell@enron.com
To: carmen.chavira@enron.com
Subject: Retro
Mime-Version: 1.0
Content-Type: text/plain; charset=us-ascii
Content-Transfer-Encoding: 7bit
X-From: Larry F Campbell
X-To: Carmen Chavira
X-cc: 
X-bcc: 
X-Folder: \Larry_Campbell_Dec2000\Notes Folders\'sent mail
X-Origin: Campbell-L
X-FileName: lcampbel.nsf

Carmen---

My night differential has not posted to my last four paychecks.
The last time I received it was for pay period ending 05/15/2000.
Would you please include a retro adjustment to my next check?


LC
522-94-9373
x3-9351


Index: 41540
SSN found: 522-94-9373
File: campbell-l/all_documents/663.

Full message:
Message-ID: <7647220.1075857842037.JavaMail.evans@thyme>
Date: Tue, 25 Jul 2000 07:43:00 -0700 (PDT)
From: larry.campbell@enron.com
To: carmen.chavira@enron.com


In [33]:
def find_credit_cards(message_str):
    msg = email.message_from_string(message_str)
    payload = msg.get_payload()
    if not payload:
        return None
    
    patterns = {
        'Visa': r'4[0-9]{12}(?:[0-9]{3})?',
        'MasterCard': r'5[1-5][0-9]{14}',
        'AmEx': r'3[47][0-9]{13}',
        'Discover': r'6(?:011|5[0-9]{2})[0-9]{12}'
    }
    
    found_cards = {}
    for card_type, pattern in patterns.items():
        matches = re.findall(pattern, payload.replace(' ', ''))
        if matches:
            found_cards[card_type] = matches
    
    return found_cards if found_cards else None

# Apply the function to all messages
df['credit_cards'] = df['message'].apply(find_credit_cards)

# Show results
cards_found = df['credit_cards'].dropna()
print(f"Found credit card numbers in {len(cards_found)} emails")

Found credit card numbers in 759 emails


In [21]:
# show me the emails with credit card numbers
for idx, cards in cards_found.items():
    print(f"\n{'='*80}")
    print(f"Index: {idx}")
    print(f"File: {df['file'][idx]}")
    print(f"\nEmail Payload:")
    msg = email.message_from_string(df['message'][idx])
    print(msg.get_payload())
    print(f"\nCredit card numbers found:")
    print(f"{'-'*80}")
    for card_type, card_numbers in cards.items():
        print(f"{card_type}: {card_numbers}")
    print(f"{'='*80}")


Index: 177
File: allen-p/_sent_mail/254.

Email Payload:
---------------------- Forwarded by Phillip K Allen/HOU/ECT on 05/30/2000 
01:32 PM ---------------------------
   
	
	
	From:  Colleen Sullivan                           05/30/2000 09:18 AM
	

To: Phillip K Allen/HOU/ECT@ECT
cc:  
Subject: Transport p&l

Phillip--
I've noticed one thing on your intra-month transport p&l that looks strange 
to me.  Remember that I do not know the Northwest at all, so this may not be 
an issue, but I'll point it out and let you decide.  Let me know if this is 
O.K. as is, so I'll know to ignore it in the future.  Also, if you want me to 
get with Kim and the Sitara people to change the mapping, let me know and 
I'll take care of it..

On PG&E NW, it appears that PGEN Kingsgate is mapped to a Malin Citygate 
curve instead of a Kingsgate curve, resulting in a total transport loss of 
$235,019.   
(If the mapping were changed, it should just reallocate p&l--not change your 
overall p&l.)  Maybe ther

#### Notes so far
- We got the dataset working 
- 517,401 emails unique emails with their own id.
- Looks like we can get a payload from all the emails with okay content.
- Found a couple of mails with SSN
- Found a couple of mails with creditcard information

##### Conclusion
The mails contain sensetive PII information that we can mask.